In [2]:
import pandas as pd
import sqlite3 
import geopy.distance
import folium
import geocoder
import html
import streamlit
import streamlit_folium


In [3]:
g = geocoder.ip('me')
print(g.latlng)

2022-05-14 23:46:15.057 INFO    geocoder.base: Requested http://ipinfo.io/json


[22.6163, 120.3133]


In [4]:
#swifter.

In [5]:
conn = sqlite3.connect("./rapidtest.sqlite")

In [6]:
df = pd.read_sql("select * from rapidtest",conn, )

In [7]:
df.Time = pd.to_datetime(df.Time)

In [8]:
pharm_list = df.groupby("Code").last().reset_index()

In [9]:
df[df.Time == df.Time.min()]

index        Code       Name                           Addr  Longitude  \
0        0  2331260016  新北市貢寮區衛生所  新北市貢寮區朝陽街７０巷１０號、新北市貢寮區仁愛路１２８號   121.9095   
1        1  2333120015  新竹縣峨眉鄉衛生所               新竹縣峨眉鄉峨眉村峨眉街２鄰５號   121.0214   
2        2  2333140017  新竹縣五峰鄉衛生所                 新竹縣五峰鄉大隘村六鄰９９號   121.1194   
3        3  2335110017  苗栗縣南庄鄉衛生所                 苗栗縣南庄鄉東村大同路１７號   121.0000   
4        4  2340170016  嘉義縣大埔鄉衛生所                 嘉義縣大埔鄉大埔村５３－１號   120.5928   
..     ...         ...        ...                            ...        ...   
764    764  5990010533      金志忠藥局                金門縣金城鎮東門里莒光路１１號   118.3183   
765    765  5990010631       大森藥局            金門縣金城鎮民生路２８、３０號１、２樓   118.3195   
766    766  5990010695       百泰藥局                  金門縣金城鎮西海路１段１號   118.2864   
767    767  5990020020       大金藥局                 金門縣金沙鎮汶沙里五福街１號   118.4130   
768    768  5990030062       大山藥局            金門縣金湖鎮新市里中正路２號、２－２號   118.4167   

     Latitude           Tel             Brand  Stock                Time  \
0    25.02258  (02)24901431  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 01:04:32   
1    24.68842   (03)5800314  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 01:04:32   
2    24.63184   (03)5851005  羅氏家用新冠病毒抗原自我檢測套組     28 2022-05-07 01:04:32   
3    24.59733   (037)822024  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 01:04:32   
4    23.29397   (05)2521214  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 01:04:32   
..        ...           ...               ...    ...                 ...   
764  24.43167   (082)325813  羅氏家用新冠病毒抗原自我檢測套組     18 2022-05-07 01:04:32   
765  24.43470    (82)325100  羅氏家用新冠病毒抗原自我檢測套組     74 2022-05-07 01:04:32   
766  24.41566   (082)312832  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 01:04:32   
767  24.48834   (082)355382  羅氏家用新冠病毒抗原自我檢測套組      1 2022-05-07 01:04:32   
768  24.44036   (082)333290  羅氏家用新冠病毒抗原自我檢測套組     57 2022-05-07 01:04:32   

                                                 Note  
0             快篩試劑販售時間為周一至周五早上9點開始販售，每日販售一箱，數量有限售完為止。  
1    本所5月13日（五）下午眼科，自5月6日起販賣快篩試劑現場排隊12時至13時止，國定及例假日不賣  
2                                                   無  
3                           口罩販賣時段:週一至週五上午8:00~下午5:00  
4                                                   無  
..                                                ...  
764                快篩實名制（分單雙號購買，星期天不分） 8:00開始販賣，售完為止。  
765                                        可直接憑健保卡買口罩  
766                           快篩實名制，每天16:00開始販售，售完為止。  
767     （以上口罩餘額很不準 詳情請洽藥局）每日早上8:00發號碼牌並於下午13:30後再來領口罩  
768                                    早上10點開始販售實名制快篩  

[769 rows x 11 columns]

In [10]:
lat = 22.649242
lon = 120.310989
center = (lat, lon)

In [11]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1345021 entries, 0 to 1345020
Data columns (total 11 columns):
 #   Column     Non-Null Count    Dtype         
---  ------     --------------    -----         
 0   index      1345021 non-null  int64         
 1   Code       1345021 non-null  object        
 2   Name       1345021 non-null  object        
 3   Addr       1345021 non-null  object        
 4   Longitude  1345021 non-null  float64       
 5   Latitude   1345021 non-null  float64       
 6   Tel        1345021 non-null  object        
 7   Brand      1345021 non-null  object        
 8   Stock      1345021 non-null  int64         
 9   Time       1345021 non-null  datetime64[ns]
 10  Note       1345021 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(2), object(6)
memory usage: 112.9+ MB


In [12]:
%%time
pharm_list['Distance'] = pharm_list.apply(lambda x: geopy.distance.distance((x.Latitude,x.Longitude), g.latlng).km, axis=1)

CPU times: user 1.02 s, sys: 128 ms, total: 1.15 s
Wall time: 1.15 s


In [16]:
pharm_list.sort_values(by='Time')

Code  index    Name                Addr  Longitude  Latitude  \
1473  5907110084    251    昱佳藥局       高雄市橋頭區仕豐南路６６號   120.3099  22.74901   
843   5903030012    189    康好藥局     臺中市大甲區三民路１３２－２號   120.6220  24.34851   
655   5901203213    199  綠杏萬芳藥局     臺北市文山區興隆路３段１１１號   121.5583  25.00031   
2829  5931112921    797    明恩藥局   新北市汐止區明峰街１７９之１號１樓   121.6286  25.06992   
1824  5912051467    468    健佑藥局    新竹市香山區大庄路４５巷２、６號   120.9284  24.78931   
...          ...    ...     ...                 ...        ...       ...   
4001  5937051730    936    青田藥局       彰化縣員林市林森路一二七號   120.5778  23.95633   
4000  5937051712    935  員林福倫藥局  彰化縣員林市和平里中山路２段１４１號   120.5711  23.96391   
3999  5937051703    934  員林健康藥局     彰化縣員林市中正路２２４號１樓   120.5747  23.95417   
4007  5937052031    940    天天藥局   彰化縣員林市鎮興里員東路一段５５號   120.5991  23.96355   
1115  5903271282    348    禾安藥局   臺中市西屯區西屯路二段１２６之８號   120.6518  24.16682   

               Tel             Brand  Stock                Time  \
1473   (07)6110302  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 06:34:34   
843   (04)26802149  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 07:04:32   
655   (02)29349516  羅氏家用新冠病毒抗原自我檢測套組     69 2022-05-07 08:35:02   
2829  (02)26923877  羅氏家用新冠病毒抗原自我檢測套組     63 2022-05-07 09:04:32   
1824   (03)5306555  羅氏家用新冠病毒抗原自我檢測套組     78 2022-05-07 09:35:02   
...            ...               ...    ...                 ...   
4001   (04)8347776  羅氏家用新冠病毒抗原自我檢測套組     16 2022-05-14 21:54:32   
4000   (04)8371218  羅氏家用新冠病毒抗原自我檢測套組      2 2022-05-14 21:54:32   
3999   (04)8396798  羅氏家用新冠病毒抗原自我檢測套組     48 2022-05-14 21:54:32   
4007   (04)8385573  羅氏家用新冠病毒抗原自我檢測套組     57 2022-05-14 21:54:32   
1115  (04)23176162  羅氏家用新冠病毒抗原自我檢測套組     25 2022-05-14 21:54:32   

                                             Note    Distance  
1473                     快篩試劑售時間:早上7:30開始發售（售完為止）   14.700405  
843   每天早上8-12點.下午14:30至售完為止.星期四不銷售. 星期日只銷售前日剩餘口罩  194.418032  
655                                             無  292.933555  
2829                                            無  302.985614  
1824                                 快篩試劑下午兩點開始販售  248.709121  
...                                           ...         ...  
4001                       物流配送時間不確定～每日的販售時間將另行公布  150.852361  
4000                             每日早上8:00販售 .售完為止  151.557456  
3999                                10月11日雙十連假有營業  150.560399  
4007               固定周一到周六上午8:30發放號碼牌，8:30開始販售口罩。  152.042921  
1115                                            無  175.170798  

[4922 rows x 12 columns]

In [14]:
sdf = df[df.Code.isin(pharm_list[pharm_list.Distance<5].Code)].groupby(['Code','Name','Addr','Tel',"Latitude","Longitude",'Note','Time']).Stock.first().unstack().fillna(0).astype(int).iloc[:,-1:].sort_values(by=df.Time.max(), ascending=False)

In [15]:
df[df.Code.isin(pharm_list[pharm_list.Distance<5].Code)].groupby(['Code','Name','Addr','Tel',"Latitude","Longitude",'Note','Time']).Stock.first().unstack().T

Code                                                    5902010025  \
Name                                                          南京藥局   
Addr                                                高雄市鹽埕區建國四路３８７號   
Tel                                                    (07)5514652   
Latitude                                                  22.63279   
Longitude                                                 120.2840   
Note                早上9:00實名制口罩販賣；實名制快篩星期1-6為下午1:00開始販賣，星期日休息，售完為止   
Time                                                                 
2022-05-07 01:04:32                                            NaN   
2022-05-07 01:34:32                                            NaN   
2022-05-07 02:04:32                                            NaN   
2022-05-07 02:34:32                                            NaN   
2022-05-07 03:04:32                                            NaN   
...                                                            ...   
2022-05-14 21:34:32                                            NaN   
2022-05-14 21:39:32                                            NaN   
2022-05-14 21:44:33                                            NaN   
2022-05-14 21:49:32                                            NaN   
2022-05-14 21:54:32                                            NaN   

Code                                                        5902010132  \
Name                                                              宏恩藥局   
Addr                                                  高雄市鹽埕區教仁里瀨南街１３３號   
Tel                                                        (07)5211318   
Latitude                                                      22.62472   
Longitude                                                     120.2823   
Note                5／10 10:30貨到開始販售 星期一至星期六10:30貨到開始販售，星期日14:00貨到開始販售   
Time                                                                     
2022-05-07 01:04:32                                                NaN   
2022-05-07 01:34:32                                                NaN   
2022-05-07 02:04:32                                                NaN   
2022-05-07 02:34:32                                                NaN   
2022-05-07 03:04:32                                                NaN   
...                                                                ...   
2022-05-14 21:34:32                                                NaN   
2022-05-14 21:39:32                                                NaN   
2022-05-14 21:44:33                                                NaN   
2022-05-14 21:49:32                                                NaN   
2022-05-14 21:54:32                                                NaN   

Code                                                             \
Name                                                              
Addr                                                              
Tel                                                               
Latitude                                                          
Longitude                                                         
Note                5／6 10:00開始販售 星期一至星期六10:00開始販售，星期日14:00開始販售   
Time                                                              
2022-05-07 01:04:32                                        36.0   
2022-05-07 01:34:32                                        36.0   
2022-05-07 02:04:32                                        36.0   
2022-05-07 02:34:32                                        36.0   
2022-05-07 03:04:32                                        36.0   
...                                                         ...   
2022-05-14 21:34:32                                         NaN   
2022-05-14 21:39:32                                         NaN   
2022-05-14 21:44:33                                         NaN   
2022-05-14 21:49:32                                         NaN   
2022-05-14 21:54:32                                     

In [210]:
ts = df[df.Code.isin(pharm_list[pharm_list.Distance<5].Code)].groupby(['Code','Name','Addr','Tel',"Latitude","Longitude",'Note','Time']).Stock.first().unstack().fillna(0).astype(int).iloc[:,-30:].stack()

In [211]:
ts = ts.reset_index()

In [212]:
ts.columns = ['Code', 'Name', 'Addr', 'Tel', 'Latitude', 'Longitude', 'Note', 'Time',"Stock"]

In [213]:
import altair as alt

In [214]:
alt.Chart(ts[ts.Code=='5907300784']).mark_line().encode(x='Time',y='Stock')

alt.Chart(...)

In [215]:
ts[ts.Code=='5907300784']

Code      Name           Addr          Tel  Latitude  Longitude  \
3660  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3661  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3662  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3663  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3664  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3665  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3666  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3667  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3668  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3669  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3670  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3671  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3672  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3673  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3674  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3675  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3676  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3677  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3678  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3679  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3680  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3681  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3682  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3683  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3684  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3685  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3686  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3687  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3688  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   
3689  5907300784  新高橋藥局博正店  高雄市左營區忠言路１８０號  (07)5509810  22.65841   120.3038   

              Note                Time  Stock  
3660  下午2:30開始販售口罩 2022-05-07 12:27:02      0  
3661  下午2:30開始販售口罩 2022-05-07 12:37:02      0  
3662  下午2:30開始販售口罩 2022-05-07 12:47:02      0  
3663  下午2:30開始販售口罩 2022-05-07 12:57:02      0  
3664  下午2:30開始販售口罩 2022-05-07 13:07:02      0  
3665  下午2:30開始販售口罩 2022-05-07 13:17:02      0  
3666  下午2:30開始販售口罩 2022-05-07 13:27:02      0  
3667  下午2:30開始販售口罩 2022-05-07 13:37:02      0  
3668  下午2:30開始販售口罩 2022-05-07 13:47:02      0  
3669  下午2:30開始販售口罩 2022-05-07 13:57:02      0  
3670  下午2:30開始販售口罩 2022-05-07 14:07:02      0  
3671  下午2:30開始販售口罩 2022-05-07 14:17:02      0  
3672  下午2:30開始販售口罩 2022-05-07 14:27:02      0  
3673  下午2:30開始販售口罩 2022-05-07 14:37:02      0  
3674  下午2:30開始販售口罩 2022-05-07 14:47:02      0  
3675  下午2:30開始販售口罩 2022-05-07 14:57:02     78  
3676  下午2:30開始販售口罩 2022-05-07 15:07:04     67  
3677  下午2:30開始販售口罩 2022-05-07 15:17:02     46  
3678  下午2:30開始販售口罩 2022-05-07 15:27:02     32  
3679  下午2:30開始販售口罩 2022-05-07 15:37:02     13  
3680  下午2:30開始販售口罩 2022-05-07 15:47:02      7  
3681  下午2:30開始販售口罩 2022-05-07 15:57:02      5  
3682  下午2:30開始販售口罩 2022-05-07 16:07:02      5  
3683  下午2:30開始販售口罩 2022-05-07 16:17:02      0  
3684  下午2:30開始販售口罩 2022-05-07 16:27:02      0  
3685  下午2:30開始販售口罩 2022-05-07 16:37:02      0  
3686  下午2:30開始販售口罩 2022-05-07 16:47:02      0  
3687  下午2:30開始販售口罩 2022-05-07 16:57:02      0  
3688  下午2:30開始販售口罩 2022-05-07 17:07:02      0  
3689  下午2:30開始販售口罩 2022-05-07 17:17:02      0

In [216]:
sdf= sdf.reset_index()

In [217]:
#sdf = df[df.Distance<2].groupby("Code").last()

In [218]:
sdf.columns[-1]

Timestamp('2022-05-07 17:17:02')

In [219]:
for i in sdf.Note:
    print(len(i),html.escape(i))


62 上午0830-1330下午1530-2100， 自2／11-2／29口罩販售周一三四五日，時間:9:00-12:00售完為止
53 營業日0900可先領取號碼牌，上午9:00-12:00及下午3:00~10:.00為販賣快篩時間，售完為止
36 每天15:30發號碼牌，於18:00前兌換完畢，逾期棄權，剩餘則繼續發放
46 早上9:00實名制口罩販賣；實名制快篩星期1-6為下午1:00開始販賣，星期日休息，售完為止
25 口罩領取時間:W1~W日（AM1100~換完為止）
1 無
21 中午12:00販售現場排隊（仕康健保藥局）
34 快篩販售因人力有限，週一、四上午9:00其餘下午2:00，週日公休。
18 週一 ~ 週六快篩 14:00 販售
35 快篩購買時間星期一至五中午12點，售完為止。 星期六、日早上九點販售。
10 快篩試劑下午2點開賣
72 快篩早上10:00開始，營業時間:（一-五）早上8:00-12:00，下午02:30-6:00（五-下午5:30休息，六-開上午半天，日-休息）
12 快篩試劑下午2:00販售
23 4／30起15:00開始販售快篩，六日皆有營業
1 無
23 快篩實名制，每天16:00開始販售，售完為止。
22 實名制快篩為下午1點-6點開放領取，領完為止
1 無
1 無
44 111／5／3近期因供貨時間不穩定.先取消上午8:40販售快篩.實際以收到貨時間開始販賣
25 快篩實名制早上8:00開始販售，人多時發放號碼牌。
23 快篩實名制，每天16:00開始販售，售完為止。
39 位於美麗島捷運站內，往西子灣方向地下二樓。販賣時間依現場公告為主，可來電詢問。
1 無
1 無
1 無
11 下午3點販售，現場排隊
32 購買實名制快篩時間下午14:00-16:00，各類防疫用品販售中
21 實名制口罩每日9:00開始販售，售完為止。
31 5／7快篩於早上8:30領取號碼牌後販賣，請從後花園排隊，謝謝
13 上午10:00開始販售快篩
33 自3／1日~3／31日，營業日08:00~21:00為販賣口罩時間
23 快篩實名制，每天16:00開始販售，售完為止。
16 實名制快篩14:00~18:00
23 快篩實名制，每天16:00開始販售，售完為止。
1 無
16 快篩販售時間 早上9點至售完為止
39 營業時間每日0

In [226]:
map_f = folium.Map(location=g.latlng, zoom_start=15, )
for r in sdf.itertuples():
    chart = alt.Chart(ts[ts.Code==r.Code],).mark_line().encode(x='Time',y='Stock').properties(title=r.Name, height=50)

    Pop = folium.Popup()
    Pop.add_child(folium.VegaLite(chart, height=30))
    #Pop.add_child(),

    folium.Marker(location=(r.Latitude, r.Longitude),
    tooltip=folium.Tooltip(f"<b>{r.Name}</b><br/>{r.Addr}<br/>{r.Tel}<br/>庫存:{r[-1]}<br/>{sdf.columns[-1]}<br/>{r.Note[:45]}"),
    popup=Pop,
    #<br/>{r.Addr}<br/>庫存:{r[-1]}<br/>{r.Note}<br/>{sdf.columns[-1]}",
    icon=folium.Icon(color="red" if r[-1]==0 else "blue", icon="fa-plus-square", prefix='fa') 
    ).add_to(map_f)
map_f